In [0]:
from pyspark.sql.functions import col, regexp_replace, when, lit
from pyspark.sql.types import StringType, IntegerType, LongType, DoubleType, DecimalType, TimestampType

path = "/Volumes/workspace/raw-zone/taxi_amarelo/"
arquivos = dbutils.fs.ls(path)

# Dicionário para renomear colunas antigas para novas
renomear_colunas = {
    "vendorid": "cod_motorista",
    "tpep_pickup_datetime": "dt_hr_inicio",
    "tpep_dropoff_datetime": "dt_hr_fim",
    "passenger_count": "qtd_pessoas",
    "trip_distance": "dist_percorrida",
    "ratecodeid": "cod_taxa",
    "store_and_fwd_flag": "ind_armazenamento",
    "pulocationid": "cod_bairro_origem",
    "dolocationid": "cod_bairro_destino",
    "payment_type": "forma_pagamento",
    "fare_amount": "vlr_taxa_corrida",
    "extra": "vlr_taxa_extra",
    "mta_tax": "vlr_taxa_mta",
    "tip_amount": "vlr_troco",
    "tolls_amount": "vlr_pedagio",
    "improvement_surcharge": "cod_taxa_melhoria",
    "total_amount": "vlr_total",
    "congestion_surcharge": "vlr_taxa_congestao",
    "airport_fee": "vlr_taxa_aeroporto",
}

# Dicionário de tipos com nomes finais das colunas
tipos_colunas = {
    "cod_motorista": StringType(),
    "dt_hr_inicio": TimestampType(),
    "dt_hr_fim": TimestampType(),
    "qtd_pessoas": IntegerType(),
    "dist_percorrida": DecimalType(10, 2),
    "cod_taxa": IntegerType(),
    "ind_armazenamento": StringType(),
    "cod_bairro_origem": StringType(),
    "cod_bairro_destino": StringType(),
    "tipo_pagamento": StringType(),
    "vlr_taxa_corrida": DecimalType(10, 2),
    "vlr_taxa_extra": DecimalType(10, 2),
    "vlr_taxa_mta": DecimalType(10, 2),
    "vlr_troco": DecimalType(10, 2),
    "vlr_pedagio": DecimalType(10, 2),
    "cod_taxa_melhoria": IntegerType(),
    "vlr_total": DecimalType(10, 2),
    "vlr_taxa_congestao": DecimalType(10, 2),
    "vlr_taxa_aeroporto": DecimalType(10, 2),
}

for i, arquivo in enumerate(arquivos, start=1):
    if arquivo.name.endswith(".parquet"):
        df = spark.read.parquet(arquivo.path)

        # Padronizar nomes para lowercase
        df = df.toDF(*[c.lower() for c in df.columns])

        # Renomear colunas
        for antigo, novo in renomear_colunas.items():
            if antigo in df.columns:
                df = df.withColumnRenamed(antigo, novo)

        # Converter para string para manipular vírgulas e pontos
        df = df.select([col(c).cast(StringType()).alias(c) for c in df.columns])

        # Substituir vírgula por ponto para decimais
        df = df.select([regexp_replace(col(c), ",", ".").alias(c) for c in df.columns])

        # Safe cast usando o dicionário com nomes finais
        for c in df.columns:
            if c in tipos_colunas:
                t = tipos_colunas[c]
                if isinstance(t, (IntegerType, LongType)):
                    df = df.withColumn(
                        c,
                        when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast("double").cast(t))
                        .otherwise(None)
                    )
                elif isinstance(t, (DecimalType, DoubleType)):
                    df = df.withColumn(
                        c,
                        when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast(t))
                        .otherwise(None)
                    )
                elif isinstance(t, TimestampType):
                    df = df.withColumn(c, col(c).cast(TimestampType()))
                else:
                    df = df.withColumn(c, col(c).cast(StringType()))

        # Adicionar coluna de origem
        df_final = df.withColumn("origem_taxi", lit("taxi_amarelo"))

        # Criar variável com nome dinâmico
        globals()[f"df_taxi_amarelo_{i}"] = df_final

        # Salvar na tabela
        df_final.write.mode("overwrite").saveAsTable("`trusted-zone`.tb_corrida_taxi_amarelo")


In [0]:
from pyspark.sql.functions import col, regexp_replace, when, lit
from pyspark.sql.types import StringType, IntegerType, LongType, DoubleType, DecimalType, TimestampType

path = "/Volumes/workspace/raw-zone/taxi_verde/"
arquivos = dbutils.fs.ls(path)

# Dicionário para renomear colunas antigas para novas
renomear_colunas = {
    "vendorid": "cod_motorista",
    "lpep_pickup_datetime": "dt_hr_inicio",
    "lpep_dropoff_datetime": "dt_hr_fim",
    "passenger_count": "qtd_pessoas",
    "trip_distance": "dist_percorrida",
    "ratecodeid": "cod_taxa",
    "store_and_fwd_flag": "ind_armazenamento",
    "pulocationid": "cod_bairro_origem",
    "dolocationid": "cod_bairro_destino",
    "payment_type": "tipo_pagamento",
    "trip_type": "tipo_viagem",
    "fare_amount": "vlr_taxa_corrida",
    "extra": "vlr_taxa_extra",
    "mta_tax": "vlr_taxa_mta",
    "tip_amount": "vlr_troco",
    "tolls_amount": "vlr_pedagio",
    "ehail_fee":"vlr_gorjeta",
    "improvement_surcharge": "cod_taxa_melhoria",
    "total_amount": "vlr_total",
    "congestion_surcharge": "vlr_taxa_congestao",
    "airport_fee": "vlr_taxa_aeroporto",
}

# Dicionário de tipos com nomes finais das colunas
tipos_colunas = {
    "cod_motorista": StringType(),
    "dt_hr_inicio": TimestampType(),
    "dt_hr_fim": TimestampType(),
    "qtd_pessoas": IntegerType(),
    "dist_percorrida": DecimalType(10, 2),
    "cod_taxa": IntegerType(),
    "ind_armazenamento": StringType(),
    "cod_bairro_origem": StringType(),
    "cod_bairro_destino": StringType(),
    "tipo_pagamento": StringType(),
    "tipo_viagem": IntegerType(),
    "vlr_taxa_corrida": DecimalType(10, 2),
    "vlr_taxa_extra": DecimalType(10, 2),
    "vlr_taxa_mta": DecimalType(10, 2),
    "vlr_troco": DecimalType(10, 2),
    "vlr_pedagio": DecimalType(10, 2),
    "vlr_gorjeta":DecimalType(10, 2),
    "cod_taxa_melhoria": IntegerType(),
    "vlr_total": DecimalType(10, 2),
    "vlr_taxa_congestao": DecimalType(10, 2),
    "vlr_taxa_aeroporto": DecimalType(10, 2),
}

for i, arquivo in enumerate(arquivos, start=1):
    if arquivo.name.endswith(".parquet"):
        df = spark.read.parquet(arquivo.path)

        # Padronizar nomes para lowercase
        df = df.toDF(*[c.lower() for c in df.columns])

        # Renomear colunas
        for antigo, novo in renomear_colunas.items():
            if antigo in df.columns:
                df = df.withColumnRenamed(antigo, novo)

        # Converter para string para manipular vírgulas e pontos
        df = df.select([col(c).cast(StringType()).alias(c) for c in df.columns])

        # Substituir vírgula por ponto para decimais
        df = df.select([regexp_replace(col(c), ",", ".").alias(c) for c in df.columns])

        # Safe cast usando o dicionário com nomes finais
        for c in df.columns:
            if c in tipos_colunas:
                t = tipos_colunas[c]
                if isinstance(t, (IntegerType, LongType)):
                    df = df.withColumn(
                        c,
                        when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast("double").cast(t))
                        .otherwise(None)
                    )
                elif isinstance(t, (DecimalType, DoubleType)):
                    df = df.withColumn(
                        c,
                        when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast(t))
                        .otherwise(None)
                    )
                elif isinstance(t, TimestampType):
                    df = df.withColumn(c, col(c).cast(TimestampType()))
                else:
                    df = df.withColumn(c, col(c).cast(StringType()))

        # Adicionar coluna de origem
        df_final = df.withColumn("origem_taxi", lit("taxi_verde"))

        # Criar variável com nome dinâmico (caso queira usar depois)
        globals()[f"df_taxi_verde_{i}"] = df_final

        # Salvar na tabela
        df_final.write.mode("overwrite").option("mergeSchema", "true").saveAsTable("`trusted-zone`.tb_corrida_taxi_verde")


In [0]:
display(df_taxi_verde_5)

cod_motorista lpep_pickup_datetime lpep_dropoff_datetime ind_armazenamento cod_taxa cod_bairro_origem cod_bairro_destino qtd_pessoas dist_percorrida vlr_taxa_corrida vlr_taxa_extra vlr_taxa_mta vlr_troco vlr_pedagio vlr_gorjeta cod_taxa_melhoria vlr_total forma_pagamento trip_type vlr_taxa_congestao origem_taxi 2 2023-03-01 00:25:10 2023-03-01 00:35:47 N 1 82 196 1 2.36 13.50 1.00 0.50 0.00 0.00 null 1 16.00 2 1 0.00 taxi_verde 2 2023-03-01 00:14:29 2023-03-01 00:25:04 N 1 7 7 1 0.78 null null null 0.00 0.00 null null null 3 1 0.00 taxi_verde 2 2023-03-01 00:14:29 2023-03-01 00:25:04 N 1 7 7 1 0.78 6.50 1.00 0.50 0.00 0.00 null 1 9.00 3 1 0.00 taxi_verde 2 2023-02-28 22:59:46 2023-02-28 23:08:38 N 1 166 74 1 1.66 11.40 1.00 0.50 2.78 0.00 null 1 16.68 1 1 0.00 taxi_verde 2 2023-03-01 00:54:03 2023-03-01 01:03:14 N 1 236 229 1 3.14 15.60 1.00 0.50 4.17 0.00 null 1 25.02 1 1 2.75 taxi_verde 2 2023-03-01 01:00:09 2023-03-01 01:14:37 N 1 75 235 1 5.69 23.30 1.00 0.50 4.00 0.00 null 1 29.80 1 1 0.00 taxi_verde 2 2023-03-01 00:09:45 2023-03-01 00:26:06 N 1 260 160 1 2.92 17.70 1.00 0.50 4.04 0.00 null 1 24.24 1 1 0.00 taxi_verde 2 2023-03-01 00:39:30 2023-03-01 00:39:33 N 5 95 264 5 0.00 35.00 0.00 0.00 1.00 0.00 null 1 37.00 1 2 0.00 taxi_verde 2 2023-03-01 00:03:07 2023-03-01 00:14:44 N 1 244 41 1 3.34 16.30 1.00 0.50 5.64 0.00 null 1 24.44 1 1 0.00 taxi_verde 2 2023-03-01 00:42:56 2023-03-01 00:49:57 N 1 83 7 5 1.75 10.70 1.00 0.50 2.64 0.00 null 1 15.84 1 1 0.00 taxi_verde 2 2023-03-01 01:13:10 2023-03-01 01:15:50 N 1 223 223 1 0.74 5.10 1.00 0.50 1.52 0.00 null 1 9.12 1 1 0.00 taxi_verde 2 2023-03-01 00:28:03 2023-03-01 00:32:46 N 1 260 260 1 0.63 6.50 1.00 0.50 1.80 0.00 null 1 10.80 1 1 0.00 taxi_verde 2 2023-03-01 00:22:23 2023-03-01 00:42:34 N 1 82 193 1 2.94 19.80 1.00 0.50 0.00 0.00 null 1 22.30 2 1 0.00 taxi_verde 2 2023-03-01 00:49:20 2023-03-01 00:53:08 N 1 146 145 1 0.36 null null null 0.00 0.00 null null null 3 1 0.00 taxi_verde 2 2023-03-01 00:49:20 2023-03-01 00:53:08 N 1 146 145 1 0.36 5.80 1.00 0.50 0.00 0.00 null 1 8.30 3 1 0.00 taxi_verde 2 2023-03-01 00:29:28 2023-03-01 00:44:24 N 1 130 191 1 3.59 19.10 1.00 0.50 4.32 0.00 null 1 25.92 1 1 0.00 taxi_verde 2 2023-03-01 00:41:05 2023-03-01 00:49:25 N 1 95 134 1 2.00 11.40 1.00 0.50 0.00 0.00 null 1 13.90 2 1 0.00 taxi_verde 2 2023-03-01 00:25:47 2023-03-01 00:34:16 N 1 74 152 1 1.63 10.70 1.00 0.50 2.64 0.00 null 1 15.84 1 1 0.00 taxi_verde 2 2023-03-01 00:32:41 2023-03-01 00:44:14 N 1 95 173 1 2.38 14.20 1.00 0.50 4.18 0.00 null 1 20.88 1 1 0.00 taxi_verde 2 2023-03-01 00:52:41 2023-03-01 01:13:37 N 1 210 155 1 3.65 21.20 1.00 0.50 0.00 0.00 null 1 23.70 2 1 0.00 taxi_verde 2 2023-03-01 00:50:46 2023-03-01 00:57:26 N 1 260 82 2 1.02 8.60 1.00 0.50 3.33 0.00 null 1 14.43 1 1 0.00 taxi_verde 1 2023-03-01 00:41:46 2023-03-01 00:45:35 N 1 82 82 1 0.90 6.50 1.00 1.50 1.80 0.00 null 1 10.80 1 1 0.00 taxi_verde 2 2023-03-01 00:05:21 2023-03-01 00:11:48 N 1 82 82 5 1.21 8.60 1.00 0.50 0.00 0.00 null 1 11.10 2 1 0.00 taxi_verde 2 2023-03-01 00:17:04 2023-03-01 00:21:07 N 1 179 179 1 0.56 5.80 1.00 0.50 2.00 0.00 null 1 10.30 1 1 0.00 taxi_verde 2 2023-03-01 00:21:07 2023-03-01 00:40:15 N 1 130 139 1 5.32 25.40 1.00 0.50 0.00 0.00 null 1 27.90 1 1 0.00 taxi_verde 2 2023-03-01 00:00:37 2023-03-01 00:29:43 N 1 127 119 1 7.40 26.50 0.50 0.50 0.00 0.00 null 0 27.80 2 1 0.00 taxi_verde 2 2023-03-01 00:22:51 2023-03-01 00:31:18 N 1 75 247 1 3.25 14.90 1.00 0.50 0.00 0.00 null 1 17.40 2 1 0.00 taxi_verde 2 2023-03-01 01:14:28 2023-03-01 01:40:08 N 5 83 186 2 6.64 40.00 0.00 0.00 0.00 0.00 null 1 43.75 1 2 2.75 taxi_verde 1 2023-03-01 01:31:33 2023-03-01 02:03:54 N 1 216 41 1 0.00 45.50 0.00 1.50 0.00 6.55 null 1 53.55 1 1 0.00 taxi_verde 2 2023-03-01 01:17:00 2023-03-01 01:42:28 N 1 83 124 1 7.09 33.10 1.00 0.50 7.12 0.00 null 1 42.72 1 1 0.00 taxi_verde 2 2023-03-01 00:09:47 2023-03-01 00:15:47 N 1 75 41 1 1.62 9.30 1.00 0.50 2.36 0.00 null 1 14.16 1 1 0.00 taxi_verde 2 2023-0

In [0]:

from pyspark.sql.functions import col, when
from pyspark.sql.types import IntegerType, LongType, DecimalType, DoubleType, TimestampType, StringType

# exemplo de df
df = spark.createDataFrame([
    ("1.0", "2023-08-01 10:00:00"),
    ("2.5", "2023-08-01 11:00:00"),
    ("abc", "invalid")
], ["qtd_pessoas", "dt_hr_inicio"])

tipos_colunas = {
    "qtd_pessoas": IntegerType(),
    "dt_hr_inicio": TimestampType()
}

for c in df.columns:
    if c in tipos_colunas:
        t = tipos_colunas[c]
        tipo_t = type(t)
        if tipo_t == IntegerType or tipo_t == LongType:
            df = df.withColumn(
                c,
                when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast("double").cast(t))
                .otherwise(None)
            )
        elif tipo_t == DecimalType or tipo_t == DoubleType:
            df = df.withColumn(
                c,
                when(col(c).rlike(r"^[0-9]+(\.[0-9]+)?$"), col(c).cast(t))
                .otherwise(None)
            )
        elif tipo_t == TimestampType:
            df = df.withColumn(c, col(c).cast(TimestampType()))
        else:
            df = df.withColumn(c, col(c).cast(StringType()))

df.printSchema()
df.show()


root
 |-- qtd_pessoas: integer (nullable = true)
 |-- dt_hr_inicio: timestamp (nullable = true)



---------------------------------------------------------------------------
DateTimeException                         Traceback (most recent call last)
File <command-7565651743343005>, line 38
     35             df = df.withColumn(c, col(c).cast(StringType()))
     37 df.printSchema()
---> 38 df.show()

File /databricks/python/lib/python3.11/site-packages/pyspark/sql/connect/dataframe.py:1193, in DataFrame.show(self, n, truncate, vertical)
   1192 def show(self, n: int = 20, truncate: Union[bool, int] = True, vertical: bool = False) -> None:
-> 1193     print(self._show_string(n, truncate, vertical))

File /databricks/python/lib/python3.11/site-packages/pyspark/sql/connect/dataframe.py:934, in DataFrame._show_string(self, n, truncate, vertical)
    917     except ValueError:
    918         raise PySparkTypeError(
    919             error_class="NOT_BOOL",
    920             message_parameters={
   (...)
    923             },
    924         )
    926 table, _ = DataFrame(
    927 

In [0]:
from pyspark.sql.functions import col

df = spark.read.parquet(arquivo.path)

filtered_df = df.filter(col("ehail_fee").isNotNull())
display(filtered_df)

VendorID lpep_pickup_datetime lpep_dropoff_datetime store_and_fwd_flag RatecodeID PULocationID DOLocationID passenger_count trip_distance fare_amount extra mta_tax tip_amount tolls_amount ehail_fee improvement_surcharge total_amount payment_type trip_type congestion_surcharge

In [0]:
from pyspark.sql.functions import col

display(df)#.filter(col("passenger_count").like("%1.0%")).select("passenger_count"))